In [54]:
import numpy as np
import random
import math
from typing import Tuple, Literal, Union, Optional, List, Dict, NamedTuple, Callable, Any, Set
from queue import Queue
import warnings
import sys
import json
import time
import types
import pickle
import plotly.graph_objs as go
import plotly.express as px
import pandas as pd
import os
from eoh.problems.optimization.classic_benchmark_path_planning.utils.benchmark import MultiMapBenchmarker

In [55]:
pd.set_option('display.max_rows', None)     # 모든 행 표시
pd.set_option('display.max_columns', None)  # 모든 열 표시
pd.set_option('display.width', None)        # 가로 폭 제한 없음
pd.set_option('display.max_colwidth', None) # 셀 내용 잘림 없이 표시
pd.options.display.float_format = "{:.3f}".format 

In [4]:
class Map(NamedTuple):
    grid: np.ndarray
    start: Union[Tuple[float, float], Tuple[float, float, float]]
    goal: Union[Tuple[float, float], Tuple[float, float, float]]
    obstacles: List[Union[Tuple[float, float, float, float], Tuple[float, float, float, float, float, float]]] # x, y, width, height or x, y, z, width, height, dimension
    size: Union[Tuple[int, int], Tuple[int, int, int]]

class PlannerResult(NamedTuple):
    success: bool
    path: List[Union[Tuple[float, float], Tuple[float, float, float]]]
    nodes: List[Union[Tuple[float, float], Tuple[float, float, float]]]
    edges: List[Tuple[Tuple[float, ...], Tuple[float, ...]]]  # (parent, child)

class Node:
    def __init__(self, position, parent=None, cost=0.0):
        self.position = position
        self.parent = parent
        self.cost = cost
        self.children = []
        self.valid = True  # 장애물 충돌 여부 등


In [5]:
def visualize_map_shapes(
    map_array: np.ndarray,
    start: Optional[Tuple[int, ...]] = None,
    goal: Optional[Tuple[int, ...]] = None,
    obs:List[Tuple[int, ...]] = None,
    path: Optional[List[Tuple[float, ...]]] = None,
    nodes: Optional[List[Tuple[float, ...]]] = None,
    edges: Optional[List[Tuple[float, ...]]] = None,
    title: str = "Map Visualization"
):
    fig = go.Figure()

    if map_array.ndim == 2:
        height, width = map_array.shape
        
        for x, y, w, h in obs:
                fig.add_shape(
                    type="rect",
                    x0=x, x1=x+w, y0=y, y1=y+h,
                    fillcolor="purple",opacity=0.5,
                    line=dict(width=0)
                )

        # 방문 노드
        if nodes:
            vx, vy = zip(*nodes)
            fig.add_trace(go.Scatter(
                x=vx, y=vy, mode="markers",
                marker=dict(size=4, color="blue"),
                name="nodes"
            ))

        # 경로
        if path:
            px, py = zip(*path)
            fig.add_trace(go.Scatter(
                x=px, y=py, mode="lines+markers",
                line=dict(color="green"),
                marker=dict(size=6),
                name="Path"
            ))

        # 엣지 (연결 정보)
        if edges:
            for parent, child in edges:
                fig.add_trace(go.Scatter(
                    x=[parent.position[0], child.position[0]], y=[parent.position[1], child.position[1]],
                    mode="lines",
                    line=dict(color="lightblue", width=1),
                    showlegend=False,
                    hoverinfo="skip"
                ))


        # 시작/목표
        if start:
            fig.add_trace(go.Scatter(
                x=[start[0]], y=[start[1]], mode="markers",
                marker=dict(size=10, color="red"),
                name="Start"
            ))

        if goal:
            fig.add_trace(go.Scatter(
                x=[goal[0]], y=[goal[1]], mode="markers",
                marker=dict(size=10, color="orange"),
                name="Goal"
            ))

        fig.add_shape(
            type="rect",
            x0=0, y0=0,
            x1=width, y1=height,
            line=dict(color="white", width=3),
            fillcolor="rgba(0,0,0,0)",  # 투명 내부
            layer="above"
        )

        fig.update_layout(
            title=title,
            xaxis=dict(scaleanchor="y", showgrid=False),
            # yaxis=dict(showgrid=False, autorange="reversed"),
            yaxis=dict(showgrid=False),
            height=600, width=600
        )

    elif map_array.ndim == 3:
        z, y, x = map_array.nonzero()
        x, y, z = list(x), list(y), list(z)

        # for x,y,w,h in obs:
        #     fig.add_trace(go.Mesh3d(
        #         x=x, y=y, z=z,
        #         color='black',
        #         opacity=1.0,
        #         alphahull=0,
        #         name='Obstacles'
        #     ))

        fig.add_trace(go.Mesh3d(
            x=x, y=y, z=z,
            color='black',
            opacity=1.0,
            alphahull=0,
            name='Obstacles'
        ))

        if nodes:
            vx, vy, vz = zip(*nodes)
            fig.add_trace(go.Scatter3d(
                x=vx, y=vy, z=vz,
                mode='markers',
                marker=dict(size=2, color='blue'),
                name='Visited'
            ))

        # 엣지 (연결 정보)
        if edges:
            for parent, child in edges:
                fig.add_trace(go.Scatter3d(
                    x=[parent.position[0], child.position[0]],
                    y=[parent[1].position, child.position[1]],
                    z=[parent[2].position, child.position[2]],
                    mode='lines',
                    line=dict(color='lightblue', width=2),
                    showlegend=False,
                    hoverinfo="skip"
                ))

        if path:
            px_, py_, pz_ = zip(*path)
            fig.add_trace(go.Scatter3d(
                x=px_, y=py_, z=pz_,
                mode='lines+markers',
                marker=dict(size=3, color='green'),
                name='Path'
            ))

        if start:
            fig.add_trace(go.Scatter3d(
                x=[start[0]], y=[start[1]], z=[start[2]],
                mode='markers',
                marker=dict(size=5, color='red'),
                name='Start'
            ))

        if goal:
            fig.add_trace(go.Scatter3d(
                x=[goal[0]], y=[goal[1]], z=[goal[2]],
                mode='markers',
                marker=dict(size=5, color='orange'),
                name='Goal'
            ))

        fig.update_layout(
            title=title,
            scene=dict(aspectmode='data'),
            height=700, width=700
        )

        

    fig.show()


In [6]:
class MapIO:
    @staticmethod
    def save_map(map_data: Map, filename: str) -> None:
        """Save Map object to a binary file."""
        with open(filename, 'wb') as f:
            pickle.dump(map_data, f)

    @staticmethod
    def load_map(filename: str) -> Map:
        """Load Map object from a binary file."""
        if not os.path.exists(filename):
            raise FileNotFoundError(f"Map file not found: {filename}")
        with open(filename, 'rb') as f:
            return pickle.load(f)

In [7]:
raw_maps = ["Maze_map_easy.pkl", "Narrow_map.pkl", "Multi_obs_map.pkl"]

multi_obs_map = MapIO.load_map("Multi_obs_map.pkl")
print("Start:", multi_obs_map.start)
print("Obstacles:", len(multi_obs_map.obstacles))
print(multi_obs_map.grid.shape)

hard_maze_map = MapIO.load_map("Maze_map.pkl")
print("Start:", hard_maze_map.start)
print("Obstacles:", len(hard_maze_map.obstacles))
print(hard_maze_map.grid.shape)

maze_map = MapIO.load_map("Maze_map_easy.pkl")
print("Start:", maze_map.start)
print("Obstacles:", len(maze_map.obstacles))
print(maze_map.grid.shape)

narrow_map = MapIO.load_map("Narrow_map.pkl")
print("Start:", narrow_map.start)
print("Obstacles:", len(narrow_map.obstacles))
print(narrow_map.grid.shape)

Start: (1, 1)
Obstacles: 35
(100, 100)
Start: (29, 40)
Obstacles: 8
(100, 100)
Start: (29, 10)
Obstacles: 5
(100, 100)
Start: (80, 50)
Obstacles: 5
(100, 100)


In [8]:
maps=[multi_obs_map, maze_map, narrow_map]
# maps=[multi_obs_map, hard_maze_map, maze_map, narrow_map]

In [9]:
json_path = './eoh/src/eoh/problems/optimization/classic_benchmark_path_planning/utils/classic_method__.json'
with open(json_path, "r") as f:
    classic_method = json.load(f)

print(classic_method[0].keys())

dict_keys(['algorithm', 'algorithm_description', 'planning_mechanism', 'code'])


In [10]:
import_string ='''
from typing import Tuple, Literal, Union, Optional, List, Dict, NamedTuple, Callable, Any, Set, TYPE_CHECKING, Type
import time
from queue import Queue
import numpy as np
import random
import math
import sys
import os
from eoh.problems.optimization.classic_benchmark_path_planning.utils.architecture_utils import PlannerResult, Map
'''

In [ ]:
def get_exp_result(path, ref_avg, time_limit=None, length_limit=None, is_or=False):
    if not os.path.exists(path):
        return pd.DataFrame()
    
    with open(path, "r") as f:
        data = json.load(f)
        filtered_sorted_algorithms = sorted(
        [alg for alg in data if alg.get('operator') != 'initial'],
        key=lambda x: x.get('objective', float('inf'))
        )

    print(len(filtered_sorted_algorithms))

    # ref_avg 앞에서 선언됨
    benchmarker = MultiMapBenchmarker(maps=maps, iter=100)

    g_total_df = pd.DataFrame()

    for i, method in enumerate(filtered_sorted_algorithms):
        print(f"Evaluating method {i+1}/{len(filtered_sorted_algorithms)}: {method['objective']}")
        if method['success_rate'] < 1.0:continue
        if is_or:
            if not (method['time_improvement'] >= time_limit or method['length_improvement'] >= length_limit):
                continue
        else:
            if time_limit:
                if not method['time_improvement'] >= time_limit:
                    continue
                
            if length_limit:
                if not method['length_improvement'] >= length_limit:
                    continue
            
            
        code_string = method['code']
        namedf = pd.DataFrame()
        namedf['alg_name'] = [method['objective']]* len(maps)
        with warnings.catch_warnings():
            warnings.simplefilter("ignore")
            planning_module = types.ModuleType("planning_module")
            exec(import_string+code_string, planning_module.__dict__)
            sys.modules[planning_module.__name__] = planning_module
            try:
                planner = planning_module.Planner(max_iter=5000)
            except:
                continue
            res, avg_rest = benchmarker.run(planner.plan)

            if avg_rest is None: continue
            imp_res = MultiMapBenchmarker.get_improvement(ref_avg, avg_rest)

            res_df = pd.concat([namedf, avg_rest, imp_res], axis=1)
            g_total_df = pd.concat([g_total_df, res_df], axis=0)

    return g_total_df

In [12]:
benchmarker = MultiMapBenchmarker(maps=maps, iter=100)

total_df = pd.DataFrame()

for method in classic_method:
    code_string = method['code']
    namedf = pd.DataFrame()
    namedf['alg_name'] = [method['algorithm']]* len(maps)
    with warnings.catch_warnings():
        warnings.simplefilter("ignore")
        planning_module = types.ModuleType("planning_module")
        exec(import_string+code_string, planning_module.__dict__)
        sys.modules[planning_module.__name__] = planning_module
        planner = planning_module.Planner(max_iter=5000)
        res, avg_rest = benchmarker.run(planner.plan)
        if method['algorithm'] == 'RRT':
            ref_avg = avg_rest
            
        if avg_rest is None: continue
        imp_res = MultiMapBenchmarker.get_improvement(ref_avg, avg_rest)

        res_df = pd.concat([namedf, avg_rest, imp_res], axis=1)
        total_df = pd.concat([total_df, res_df], axis=0)

total_df


[2025.09.22 - 12:27:42] Map 1
Iteration 1: Time taken: 0.0249 seconds, Success: True
Iteration 2: Time taken: 0.0223 seconds, Success: True
Iteration 3: Time taken: 0.0405 seconds, Success: True
Iteration 4: Time taken: 0.0200 seconds, Success: True
Iteration 5: Time taken: 0.0120 seconds, Success: True
Iteration 6: Time taken: 0.0110 seconds, Success: True
Iteration 7: Time taken: 0.0110 seconds, Success: True
Iteration 8: Time taken: 0.0485 seconds, Success: True
Iteration 9: Time taken: 0.0264 seconds, Success: True
Iteration 10: Time taken: 0.0565 seconds, Success: True
Iteration 11: Time taken: 0.0260 seconds, Success: True
Iteration 12: Time taken: 0.0240 seconds, Success: True
Iteration 13: Time taken: 0.0240 seconds, Success: True
Iteration 14: Time taken: 0.0481 seconds, Success: True
Iteration 15: Time taken: 0.0321 seconds, Success: True
Iteration 16: Time taken: 0.0165 seconds, Success: True
Iteration 17: Time taken: 0.0135 seconds, Success: True
Iteration 18: Time taken: 0

alg_name  map_id  success_rate  time_avg  num_nodes_avg  \
0                          RRT       0         1.000     0.034        461.980   
1                          RRT       1         1.000     0.203       1637.590   
2                          RRT       2         1.000     0.069        859.410   
0                         RRT*       0         1.000     0.073        447.980   
1                         RRT*       1         1.000     0.411       1630.000   
2                         RRT*       2         1.000     0.125        796.670   
0                  RRT-Connect       0         1.000     0.009        106.120   
1                  RRT-Connect       1         1.000     0.015        236.560   
2                  RRT-Connect       2         1.000     0.019        251.010   
0                 RRT*-Connect       0         1.000     0.012        129.620   
1                 RRT*-Connect       1         1.000     0.020        263.170   
2                 RRT*-Connect       2         1.000     0.028        288.330   
0                       BI-RRT       0         1.000     0.003         72.900   
1                       BI-RRT       1         1.000     0.009        228.860   
2                       BI-RRT       2         1.000     0.008        163.750   
0                      BI-RRT*       0         1.000     0.019         83.310   
1                      BI-RRT*       1         1.000     0.034        240.330   
2                      BI-RRT*       2         1.000     0.029        203.750   
0                Informed-RRT*       0         1.000     0.291        726.890   
1                Informed-RRT*       1         1.000     0.352       1218.830   
2                Informed-RRT*       2         1.000     0.185        845.480   
0        Informed-RRT*-Connect       0         1.000     0.811        471.140   
1        Informed-RRT*-Connect       1         1.000     0.441        589.120   
2        Informed-RRT*-Connect       2         1.000     0.619        563.160   
0  Bidirectional-Informed-RRT*       0         1.000     0.194        440.850   
1  Bidirectional-Informed-RRT*       1         1.000     0.102        508.970   
2  Bidirectional-Informed-RRT*       2         1.000     0.140        551.000   
0        Improved-RRT*-Connect       0         1.000     0.142        334.000   
1        Improved-RRT*-Connect       1         1.000     0.139        644.380   
2        Improved-RRT*-Connect       2         1.000     0.145        578.110   

   path_length_avg  smoothness_avg  success_improvement  time_improvement  \
0          188.081           0.006                0.000            -0.000   
1          303.969           0.004                0.000            -0.000   
2          150.713           0.008                0.000            -0.000   
0          157.771           0.015                0.000          -115.630   
1          225.666           0.011                0.000          -102.355   
2          116.530           0.021                0.000           -82.809   
0          195.986           0.011                0.000            73.291   
1          302.132           0.007                0.000            92.609   
2          160.833           0.014                0.000            71.705   
0          171.903           0.017                0.000            65.419   
1          258.288           0.011                0.000            90.102   
2          133.799           0.022                0.000            58.649   
0          179.647           0.011                0.000            90.563   
1          305.361           0.006                0.000            95.493   
2          156.816           0.013                0.000            88.337   
0          165.592           0.018                0.000            44.127   
1          264.277           0.010                0.000            83.102   
2          130.652           0.022                0.000            57.039   
0          149.971           0.029             

In [13]:
# classic method result
grouped_avg = total_df.groupby('alg_name').mean().reset_index()
a = pd.DataFrame(grouped_avg)
a['method'] = a['alg_name']
a

alg_name  map_id  success_rate  time_avg  num_nodes_avg  \
0                       BI-RRT   1.000         1.000     0.007        155.170   
1                      BI-RRT*   1.000         1.000     0.028        175.797   
2  Bidirectional-Informed-RRT*   1.000         1.000     0.145        500.273   
3        Improved-RRT*-Connect   1.000         1.000     0.142        518.830   
4                Informed-RRT*   1.000         1.000     0.276        930.400   
5        Informed-RRT*-Connect   1.000         1.000     0.624        541.140   
6                          RRT   1.000         1.000     0.102        986.327   
7                         RRT*   1.000         1.000     0.203        958.217   
8                 RRT*-Connect   1.000         1.000     0.020        227.040   
9                  RRT-Connect   1.000         1.000     0.014        197.897   

   path_length_avg  smoothness_avg  success_improvement  time_improvement  \
0          213.941           0.010                0.000            91.464   
1          186.840           0.017                0.000            61.423   
2          171.860           0.030                0.000          -176.173   
3          170.811           0.030                0.000          -133.800   
4          161.983           0.031                0.000          -335.135   
5          165.451           0.045                0.000         -1075.182   
6          214.254           0.006                0.000             0.000   
7          166.656           0.016                0.000          -100.265   
8          187.997           0.016                0.000            71.390   
9          219.650           0.011                0.000            79.202   

   node_improvement  length_improvement  smoothness_improvement  \
0            83.730              -0.008                  67.327   
1            81.194              12.775                 180.717   
2            36.460              19.815                 389.512   
3            40.362              19.889                 394.092   
4           -10.050              23.838                 415.824   
5            32.171              22.505                 634.563   
6             0.000               0.000                   0.000   
7             3.598              21.519                 162.074   
8            74.107              11.617                 176.693   
9            77.792              -3.438                  82.247   

   objective_score                       method  
0           27.771                       BI-RRT  
1           26.996                      BI-RRT*  
2          -39.015  Bidirectional-Informed-RRT*  
3          -26.236        Improved-RRT*-Connect  
4          -84.159                Informed-RRT*  
5         -305.879        Informed-RRT*-Connect  
6            0.000                          RRT  
7          -16.358                         RRT*  
8           29.271                 RRT*-Connect  
9           22.109                  RRT-Connect

In [152]:
total_df[total_df['map_id']==2].sort_values(by='time_improvement', ascending=False)

alg_name  map_id  success_rate  time_avg  num_nodes_avg  \
2                       BI-RRT       2         1.000     0.008        163.750   
2                  RRT-Connect       2         1.000     0.020        251.010   
2                 RRT*-Connect       2         1.000     0.029        288.330   
2                      BI-RRT*       2         1.000     0.031        203.750   
2                          RRT       2         1.000     0.071        859.410   
2                         RRT*       2         1.000     0.128        796.670   
2  Bidirectional-Informed-RRT*       2         1.000     0.142        551.000   
2        Improved-RRT*-Connect       2         1.000     0.147        578.110   
2                Informed-RRT*       2         1.000     0.189        845.480   
2        Informed-RRT*-Connect       2         1.000     0.628        563.160   

   path_length_avg  smoothness_avg  success_improvement  time_improvement  \
2          156.816           0.013                0.000            88.262   
2          160.833           0.014                0.000            72.231   
2          133.799           0.022                0.000            59.461   
2          130.652           0.022                0.000            56.966   
2          150.713           0.008                0.000            -0.000   
2          116.530           0.021                0.000           -80.128   
2          119.867           0.039                0.000          -100.237   
2          120.179           0.039                0.000          -107.371   
2          114.244           0.041                0.000          -166.080   
2          115.419           0.069                0.000          -784.376   

   node_improvement  length_improvement  smoothness_improvement  \
2            80.946              -4.049                  64.971   
2            70.793              -6.715                  81.963   
2            66.450              11.223                 173.670   
2            76.292              13.311                 182.648   
2            -0.000              -0.000                   0.000   
2             7.300              22.681                 166.805   
2            35.886              20.467                 400.656   
2            32.732              20.260                 400.185   
2             1.621              24.198                 426.151   
2            34.471              23.418                 771.031   

   objective_score  
2           24.374  
2           18.050  
2           25.440  
2           25.990  
2            0.000  
2           -9.596  
2          -15.788  
2          -18.055  
2          -33.174  
2         -217.407

In [64]:
exp_path_dict = dict()
exp_path_dict['eoh'] = "./path_planning/exp_result/basic_eoh_from_ma.json"
exp_path_dict['expert'] = "./path_planning/mobj/results/pops/population_generation_9.json"
exp_path_dict['analysis'] = "./path_planning/mobj_analysis/results/pops/population_generation_15.json"
exp_path_dict['ma1'] = "./paper_result/interactive_multi_agent1/results/pops/population_generation_8.json"
exp_path_dict['ma2'] = "./paper_result/interactive_multi_agent2/results/pops/population_generation_10.json"
# exp_path_dict['ma3'] = "./paper_result/interactive_multi_agent3/results/pops/population_generation_15.json"
# exp_path_dict['ma4'] = "./paper_result/interactive_multi_agent4/results/pops/population_generation_15.json"
# exp_path_dict['ma5'] = "./paper_result/interactive_multi_agent5/results/pops/population_generation_23.json"
# exp_path_dict['ma6'] = "./paper_result/interactive_multi_agent_ref_perform/results/pops/population_generation_10.json"
exp_path_dict['gpt5'] = "./paper_result/interactive_multi_agent_gpt5/results/pops/population_generation_9.json"

In [ ]:
result_dfs = {}

for k, path in exp_path_dict.items():
    res = get_exp_result(path, ref_avg)
    result_dfs[k] = res

18
Evaluating method 1/18: -7.79662
[2025.09.26 - 14:21:30] Map 1
Iteration 1: Time taken: 0.0109 seconds, Success: True
Iteration 2: Time taken: 0.0051 seconds, Success: True
Iteration 3: Time taken: 0.0116 seconds, Success: True
Iteration 4: Time taken: 0.0134 seconds, Success: True
Iteration 5: Time taken: 0.0000 seconds, Success: True
Iteration 6: Time taken: 0.0154 seconds, Success: True
Iteration 7: Time taken: 0.0000 seconds, Success: True
Iteration 8: Time taken: 0.0000 seconds, Success: True
Iteration 9: Time taken: 0.0194 seconds, Success: True
Iteration 10: Time taken: 0.0086 seconds, Success: True
Iteration 11: Time taken: 0.0089 seconds, Success: True
Iteration 12: Time taken: 0.0020 seconds, Success: True
Iteration 13: Time taken: 0.0105 seconds, Success: True
Iteration 14: Time taken: 0.0169 seconds, Success: True
Iteration 15: Time taken: 0.0010 seconds, Success: True
Iteration 16: Time taken: 0.0000 seconds, Success: True
Iteration 17: Time taken: 0.0136 seconds, Succe

In [47]:
k = 'gpt5'
path = exp_path_dict[k]
res = get_exp_result(path, ref_avg)
result_dfs[k] = res

[2025.09.23 - 12:47:38] Map 1
Iteration 1: Time taken: 0.0065 seconds, Success: True
Iteration 2: Time taken: 0.0070 seconds, Success: True
Iteration 3: Time taken: 0.0061 seconds, Success: True
Iteration 4: Time taken: 0.0070 seconds, Success: True
Iteration 5: Time taken: 0.0071 seconds, Success: True
Iteration 6: Time taken: 0.0060 seconds, Success: True
Iteration 7: Time taken: 0.0050 seconds, Success: True
Iteration 8: Time taken: 0.0093 seconds, Success: True
Iteration 9: Time taken: 0.0000 seconds, Success: True
Iteration 10: Time taken: 0.0000 seconds, Success: True
Iteration 11: Time taken: 0.0069 seconds, Success: True
Iteration 12: Time taken: 0.0009 seconds, Success: True
Iteration 13: Time taken: 0.0121 seconds, Success: True
Iteration 14: Time taken: 0.0000 seconds, Success: True
Iteration 15: Time taken: 0.0144 seconds, Success: True
Iteration 16: Time taken: 0.0000 seconds, Success: True
Iteration 17: Time taken: 0.0000 seconds, Success: True
Iteration 18: Time taken: 0

In [22]:
result_dfs.keys()

dict_keys(['eoh', 'expert', 'analysis', 'ma1', 'ma2', 'gpt5'])

In [48]:
frames = list()
raw_frames = list()

for k, df in result_dfs.items():
    grouped_df = df.groupby('alg_name').mean(numeric_only=True).reset_index()
    grouped_df['method'] = k
    frames.append(grouped_df)
    df['method'] = k
    raw_frames.append(df)

merged_df = pd.concat([a]+frames, ignore_index=True, axis=0)
raw_merged_df = pd.concat(raw_frames, ignore_index=True, axis=0)

In [49]:
raw_merged_df[raw_merged_df['map_id']==2].sort_values(by='time_improvement', ascending=False)

alg_name  map_id  success_rate  time_avg  num_nodes_avg  path_length_avg  \
449   -42.620       2         1.000     0.002         30.000          125.190   
542   -33.377       2         1.000     0.007         52.000          128.227   
548   -33.039       2         1.000     0.010         48.000          145.043   
461   -40.037       2         1.000     0.010         75.000          117.012   
515   -35.390       2         1.000     0.010        199.420          144.998   
491   -37.181       2         1.000     0.010         74.000          136.541   
530   -34.292       2         0.990     0.010        140.740          143.157   
458   -40.134       2         1.000     0.014         79.000          115.018   
47    -14.136       2         1.000     0.014        196.260          139.166   
518   -35.319       2         1.000     0.014         93.000          115.617   
554   -32.875       2         1.000     0.014         75.000          139.452   
89     -6.332       2         1.000     0.015        196.720          124.264   
476   -38.511       2         1.000     0.015        140.000          121.594   
551   -32.968       2         1.000     0.015        187.190          133.474   
497   -36.947       2         1.000     0.016         74.000          135.282   
56     -9.557       2         1.000     0.016        203.250          138.210   
65     -7.553       2         1.000     0.016        160.640          126.593   
545   -33.079       2         1.000     0.017         87.000          121.875   
473   -39.022       2         1.000     0.017         82.000          122.672   
416   -32.055       2         1.000     0.017        179.120          123.063   
539   -33.560       2         1.000     0.017         90.000          123.587   
80     -6.658       2         1.000     0.017        177.290          127.760   
500   -36.918       2         1.000     0.017         92.000          132.851   
395   -33.518       2         1.000     0.018        219.510          122.638   
104   -29.434       2         1.000     0.018        202.310          125.454   
62     -8.936       2         1.000     0.018        216.610          140.449   
140   -26.659       2         1.000     0.018        202.700          125.970   
488   -37.295       2         1.000     0.018         81.000          125.196   
44    -15.039       2         1.000     0.018        224.820          147.925   
359   -35.998       2         1.000     0.018        180.570          124.101   
77     -6.683       2         0.830     0.019        242.680          123.654   
383   -34.186       2         1.000     0.019        187.170          122.119   
269   -33.274       2         1.000     0.019        259.080          126.215   
512   -35.788       2         0.970     0.019        116.660          131.087   
377   -34.246       2         1.000     0.019        264.990          124.649   
281   -32.762       2         1.000     0.019        268.710          124.584   
71     -6.839       2         1.000     0.020        160.730          126.138   
59     -9.239       2         1.000     0.020        237.360          149.345   
158   -26.198       2         1.000     0.020        213.850          125.687   
74     -6.778       2         1.000     0.020        221.920          144.830   
371   -35.050       2         1.000     0.020        226.580          121.172   
356   -36.213       2         1.000     0.021        188.240          122.558   
146   -26.558       2         1.000     0.021        226.200          126.163   
503   -36.768       2         1.000     0.021        161.050          128.224   
113   -28.190       2         1.000     0.021        240.510          125.446   
332   -39.020       2         1.000     0.021        242.600          122.658   
107   -29.373       2         1.000     0.021        219.030          124.467   
374   -34.761       2         1.000     0.021        201.770          122.835   
353   -36.652       2         1.000 

In [24]:
a

alg_name  map_id  success_rate  time_avg  num_nodes_avg  \
0                       BI-RRT   1.000         1.000     0.007        155.170   
1                      BI-RRT*   1.000         1.000     0.028        175.797   
2  Bidirectional-Informed-RRT*   1.000         1.000     0.145        500.273   
3        Improved-RRT*-Connect   1.000         1.000     0.142        518.830   
4                Informed-RRT*   1.000         1.000     0.276        930.400   
5        Informed-RRT*-Connect   1.000         1.000     0.624        541.140   
6                          RRT   1.000         1.000     0.102        986.327   
7                         RRT*   1.000         1.000     0.203        958.217   
8                 RRT*-Connect   1.000         1.000     0.020        227.040   
9                  RRT-Connect   1.000         1.000     0.014        197.897   

   path_length_avg  smoothness_avg  success_improvement  time_improvement  \
0          213.941           0.010                0.000            91.464   
1          186.840           0.017                0.000            61.423   
2          171.860           0.030                0.000          -176.173   
3          170.811           0.030                0.000          -133.800   
4          161.983           0.031                0.000          -335.135   
5          165.451           0.045                0.000         -1075.182   
6          214.254           0.006                0.000             0.000   
7          166.656           0.016                0.000          -100.265   
8          187.997           0.016                0.000            71.390   
9          219.650           0.011                0.000            79.202   

   node_improvement  length_improvement  smoothness_improvement  \
0            83.730              -0.008                  67.327   
1            81.194              12.775                 180.717   
2            36.460              19.815                 389.512   
3            40.362              19.889                 394.092   
4           -10.050              23.838                 415.824   
5            32.171              22.505                 634.563   
6             0.000               0.000                   0.000   
7             3.598              21.519                 162.074   
8            74.107              11.617                 176.693   
9            77.792              -3.438                  82.247   

   objective_score                       method  
0           27.771                       BI-RRT  
1           26.996                      BI-RRT*  
2          -39.015  Bidirectional-Informed-RRT*  
3          -26.236        Improved-RRT*-Connect  
4          -84.159                Informed-RRT*  
5         -305.879        Informed-RRT*-Connect  
6            0.000                          RRT  
7          -16.358                         RRT*  
8           29.271                 RRT*-Connect  
9           22.109                  RRT-Connect

In [53]:
# [(merged_df['method'].str.contains('ma', na=False)) & (merged_df['success_rate']==1.0)]
# merged_df[(merged_df['method'].str.contains('ma', na=False)) & (merged_df['success_rate']==1.0)].sort_values(by='length_improvement', ascending=False)
merged_df[(merged_df['success_rate']==1.0)].sort_values(by='time_improvement', ascending=False)

alg_name  map_id  success_rate  time_avg  \
0                         BI-RRT   1.000         1.000     0.007   
159                      -42.620   1.000         1.000     0.007   
25                       -14.136   1.000         1.000     0.012   
24                       -15.039   1.000         1.000     0.013   
28                        -9.557   1.000         1.000     0.012   
29                        -9.239   1.000         1.000     0.014   
181                      -35.390   1.000         1.000     0.010   
163                      -40.037   1.000         1.000     0.016   
30                        -8.936   1.000         1.000     0.014   
31                        -7.553   1.000         1.000     0.014   
34                        -6.778   1.000         1.000     0.015   
40                        -6.154   1.000         1.000     0.015   
26                       -11.356   1.000         1.000     0.015   
36                        -6.658   1.000         1.000     0.015   
173                      -37.181   1.000         1.000     0.020   
9                    RRT-Connect   1.000         1.000     0.014   
165                      -39.635   1.000         1.000     0.019   
135                      -34.246   1.000         1.000     0.015   
39                        -6.332   1.000         1.000     0.016   
62                       -26.198   1.000         1.000     0.016   
33                        -6.839   1.000         1.000     0.017   
27                       -10.572   1.000         1.000     0.016   
55                       -26.711   1.000         1.000     0.017   
41                        -6.023   1.000         1.000     0.018   
44                       -29.434   1.000         1.000     0.016   
56                       -26.659   1.000         1.000     0.016   
76                       -25.133   1.000         1.000     0.017   
161                      -40.793   1.000         1.000     0.018   
168                      -38.511   1.000         1.000     0.016   
164                      -39.958   1.000         1.000     0.019   
50                       -27.629   1.000         1.000     0.017   
121                      -38.543   1.000         1.000     0.018   
167                      -39.022   1.000         1.000     0.024   
45                       -29.373   1.000         1.000     0.018   
120                      -39.020   1.000         1.000     0.018   
123                      -38.014   1.000         1.000     0.019   
32                        -6.957   1.000         1.000     0.019   
103                      -32.762   1.000         1.000     0.019   
66                       -26.031   1.000         1.000     0.018   
58                       -26.558   1.000         1.000     0.018   
54                       -27.127   1.000         1.000     0.019   
61                       -26.352   1.000         1.000     0.018   
99                       -33.274   1.000         1.000     0.019   
171                      -37.598   1.000         1.000     0.021   
59                       -26.542   1.000         1.000     0.019   
51                       -27.527   1.000         1.000     0.019   
52                       -27.443   1.000         1.000     0.019   
12                         1.221   1.000         1.000     0.019   
47                       -28.190   1.000         1.000     0.018   
130                      -35.659   1.000         1.000     0.019   
132                      -35.479   1.000         1.000     0.019   
141                      -33.518   1.000         1.000     0.017   
193                      -32.968   1.000         1.000     0.019   
42                       -30.228   1.000         1.000     0.020   
75                       -25.368   1.000         1.000     0.019   
177                      -36.768   1.000         1.000     0.018   
149                      -31.882   1.000         1.000     0.019   
63                       -26.119   1.000         1.000     0.019   
122         

In [ ]:
# 3
print("class Node:\n    def __init__(self, position, parent=None, cost=0.0):\n        self.position = position  # Tuple[float, ...]\n        self.parent = parent      # Node or None\n        self.cost = cost          # Cost from root to this node\n        self.children = []\n\n    def add_child(self, child):\n        self.children.append(child)\n        child.parent = self\n\n    def remove_child(self, child):\n        if child in self.children:\n            self.children.remove(child)\n\n    def path_from_root(self):\n        path = []\n        node = self\n        while node is not None:\n            path.append(node.position)\n            node = node.parent\n        return path[::-1]\nclass Planner:\n    def __init__(self, max_iter=5000, step_size=5.0):\n        self.max_iter = max_iter\n        self.step_size = step_size\n        self.time_limit = 30.0\n\n        # Fixed radius for neighbor search (tuned empirically)\n        self.fixed_radius = 15.0\n\n        # Probability of sampling the goal (goal bias)\n        self.goal_sample_rate = 0.2\n\n        # Small tolerance for cost improvement\n        self.improve_tol = 1e-6\n\n        # Resolution for collision checking along edges\n        self.check_resolution = 1.0\n\n    def _is_in_obstacle(self, pos, obstacles, is_3d):\n        for obs in obstacles:\n            if is_3d:\n                x, y, z, w, h, d = obs\n                px, py, pz = pos\n                if x <= px <= x + w and y <= py <= y + h and z <= pz <= z + d:\n                    return True\n            else:\n                x, y, w, h = obs\n                px, py = pos\n                if x <= px <= x + w and y <= py <= y + h:\n                    return True\n        return False\n\n    def _is_edge_in_obstacle(self, from_pos, to_pos, obstacles, is_3d):\n        dist = 0.0\n        try:\n            dist = math.dist(from_pos, to_pos)\n        except:\n            # fallback if math.dist unavailable\n            dist = sum((f - t) ** 2 for f, t in zip(from_pos, to_pos)) ** 0.5\n        steps = max(1, int(dist / self.check_resolution))\n        for i in range(steps + 1):\n            interp = tuple(from_pos[d] + (to_pos[d] - from_pos[d]) * (i / steps) for d in range(len(from_pos)))\n            if self._is_in_obstacle(interp, obstacles, is_3d):\n                return True\n        return False\n\n    def _steer(self, from_pos, to_pos):\n        dist = 0.0\n        try:\n            dist = math.dist(from_pos, to_pos)\n        except:\n            dist = sum((f - t) ** 2 for f, t in zip(from_pos, to_pos)) ** 0.5\n        if dist <= self.step_size:\n            return to_pos\n        ratio = self.step_size / dist\n        return tuple(from_pos[i] + (to_pos[i] - from_pos[i]) * ratio for i in range(len(from_pos)))\n\n    def _dist(self, p1, p2):\n        try:\n            return math.dist(p1, p2)\n        except:\n            return sum((a - b) ** 2 for a, b in zip(p1, p2)) ** 0.5\n\n    def _sample(self, bounds, obstacles, is_3d, goal):\n        if random.random() < self.goal_sample_rate and not self._is_in_obstacle(goal, obstacles, is_3d):\n            return goal\n        while True:\n            pt = tuple(random.uniform(0, bounds[d]) for d in range(len(bounds)))\n            if not self._is_in_obstacle(pt, obstacles, is_3d):\n                return pt\n\n    def _nearest(self, tree, point):\n        best_node = None\n        best_dist = float('inf')\n        for node in tree:\n            d = self._dist(node.position, point)\n            if d < best_dist:\n                best_dist = d\n                best_node = node\n        return best_node\n\n    def _near(self, tree, point, radius):\n        res = []\n        r2 = radius * radius\n        for node in tree:\n            d = 0.0\n            if hasattr(math, 'dist'):\n                d = math.dist(node.position, point)\n            else:\n                d = sum((a - b) ** 2 for a,b in zip(node.position, point)) ** 0.5\n            if d <= radius:\n                res.append(node)\n        return res\n\n    def _update_costs_recursive(self, node):\n        for child in node.children:\n            new_cost = node.cost + self._dist(node.position, child.position)\n            if new_cost + self.improve_tol < child.cost:\n                child.cost = new_cost\n                child.parent = node\n                self._update_costs_recursive(child)\n\n    def _build_path(self, start_node, goal_node):\n        path_start = start_node.path_from_root()\n        path_goal = goal_node.path_from_root()\n        path_goal.reverse()\n        # avoid duplicate connecting node position\n        return path_start + path_goal[1:]\n\n    def _ellipsoidal_informed_sample(self, c_best, c_min, start, goal, bounds, obstacles, is_3d):\n        if c_best == float('inf') or c_best < c_min - 1e-10:\n            while True:\n                pt = tuple(random.uniform(0, bounds[d]) for d in range(len(bounds)))\n                if not self._is_in_obstacle(pt, obstacles, is_3d):\n                    return pt\n\n        dim = len(bounds)\n        center = tuple((s + g) * 0.5 for s, g in zip(start, goal))\n        a1 = tuple(g - s for s, g in zip(start, goal))\n        norm_a1 = sum(x * x for x in a1) ** 0.5\n        if norm_a1 < 1e-12:\n            while True:\n                pt = tuple(random.uniform(0, bounds[d]) for d in range(len(bounds)))\n                if not self._is_in_obstacle(pt, obstacles, is_3d):\n                    return pt\n\n        c1 = c_best * 0.5\n        c2 = (max(c_best * c_best - c_min * c_min, 0.0) ** 0.5) * 0.5\n\n        while True:\n            # Sample unit ball in dim dimension\n            rnd_dir = [random.gauss(0, 1) for _ in range(dim)]\n            norm_dir = sum(x*x for x in rnd_dir) ** 0.5\n            if norm_dir < 1e-12:\n                continue\n            unit_dir = [x / norm_dir for x in rnd_dir]\n            r = random.random() ** (1.0 / dim)\n            ball_point = [r * x for x in unit_dir]\n            # Scale sample to ellipsoid axes:\n            scaled = [c1 * ball_point[0]] + [c2 * ball_point[i] for i in range(1, dim)]\n            # Rotation aligns first axis with a1 vector (approximate)\n            dir_a1 = [x / norm_a1 for x in a1]\n            point = [center[d] + dir_a1[d] * scaled[0] for d in range(dim)]\n            for i in range(1, dim):\n                point[i] += scaled[i]\n            pt = tuple(max(0.0, min(bounds[d], point[d])) for d in range(dim))\n            if not self._is_in_obstacle(pt, obstacles, is_3d):\n                return pt\n\n    def _try_shortcut(self, path, obstacles, is_3d):\n        if len(path) <= 2:\n            return path[:]\n        smoothed_path = [path[0]]\n        idx = 0\n        n = len(path)\n        while idx < n - 1:\n            next_idx = n - 1\n            while next_idx > idx + 1:\n                if not self._is_edge_in_obstacle(path[idx], path[next_idx], obstacles, is_3d):\n                    break\n                next_idx -= 1\n            smoothed_path.append(path[next_idx])\n            idx = next_idx\n        return smoothed_path\n\n    def plan(self, map):\n        import time, math, random\n\n        bounds = map.size\n        start_pos = map.start\n        goal_pos = map.goal\n        obstacles = map.obstacles\n        is_3d = len(bounds) == 3\n\n        time_start = time.monotonic()\n\n        def timed_out():\n            return (time.monotonic() - time_start) > self.time_limit\n\n        start_root = Node(start_pos, cost=0.0)\n        goal_root = Node(goal_pos, cost=0.0)\n        tree_start = [start_root]\n        tree_goal = [goal_root]\n        nodes = [start_root, goal_root]\n        edges = []\n\n        best_path = []\n        best_cost = float('inf')\n        best_goal_node = None\n        found_solution = False\n        success_state = False\n\n        # Alternate expansions\n        for i in range(self.max_iter):\n            if timed_out():\n                break\n\n            expanding_start = (i % 2 == 0)\n            tree_a = tree_start if expanding_start else tree_goal\n            tree_b = tree_goal if expanding_start else tree_start\n            sample_goal = goal_pos if expanding_start else start_pos\n\n            sample_pt = self._sample(bounds, obstacles, is_3d, sample_goal)\n            nearest_node = self._nearest(tree_a, sample_pt)\n            new_pos = self._steer(nearest_node.position, sample_pt)\n\n            if self._is_in_obstacle(new_pos, obstacles, is_3d):\n                continue\n            if self._is_edge_in_obstacle(nearest_node.position, new_pos, obstacles, is_3d):\n                continue\n\n            radius = self.fixed_radius\n\n            near_nodes = self._near(tree_a, new_pos, radius)\n\n            min_cost = nearest_node.cost + self._dist(nearest_node.position, new_pos)\n            best_parent = nearest_node\n            for near_node in near_nodes:\n                cost_candidate = near_node.cost + self._dist(near_node.position, new_pos)\n                if cost_candidate + self.improve_tol < min_cost and not self._is_edge_in_obstacle(near_node.position, new_pos, obstacles, is_3d):\n                    min_cost = cost_candidate\n                    best_parent = near_node\n\n            new_node = Node(new_pos, parent=best_parent, cost=min_cost)\n            best_parent.add_child(new_node)\n            tree_a.append(new_node)\n            nodes.append(new_node)\n            edges.append((best_parent, new_node))\n\n            # Rewiring neighbors\n            for near_node in near_nodes:\n                if near_node == best_parent:\n                    continue\n                cost_through_new = new_node.cost + self._dist(new_node.position, near_node.position)\n                if cost_through_new + self.improve_tol < near_node.cost and not self._is_edge_in_obstacle(new_node.position, near_node.position, obstacles, is_3d):\n                    # Update edge and parent-child relations\n                    if near_node.parent:\n                        try:\n                            edges.remove((near_node.parent, near_node))\n                        except ValueError:\n                            pass\n                        near_node.parent.remove_child(near_node)\n                    near_node.parent = new_node\n                    near_node.cost = cost_through_new\n                    new_node.add_child(near_node)\n                    edges.append((new_node, near_node))\n                    # Recursively update costs of descendants\n                    self._update_costs_recursive(near_node)\n\n            # Attempt connection to opposite tree\n            nearest_other = self._nearest(tree_b, new_node.position)\n            dist_connect = self._dist(nearest_other.position, new_node.position)\n            if dist_connect <= self.step_size and not self._is_edge_in_obstacle(nearest_other.position, new_node.position, obstacles, is_3d):\n                # Connect trees by adding a connecting node\n                connect_node = Node(new_node.position, parent=nearest_other, cost=nearest_other.cost + dist_connect)\n                nearest_other.add_child(connect_node)\n                tree_b.append(connect_node)\n                nodes.append(connect_node)\n                edges.append((nearest_other, connect_node))\n\n                if expanding_start:\n                    path = self._build_path(new_node, connect_node)\n                    total_cost = new_node.cost + (connect_node.cost - nearest_other.cost)\n                else:\n                    path = self._build_path(connect_node, new_node)\n                    total_cost = connect_node.cost + (new_node.cost - best_parent.cost)\n\n                if total_cost + self.improve_tol < best_cost:\n                    best_cost = total_cost\n                    best_path = path\n                    best_goal_node = connect_node if expanding_start else new_node\n                    found_solution = True\n                    success_state = True\n                    break\n\n        # Refinement phase if solution found\n        if found_solution and best_goal_node is not None:\n            # Build a tree rooted at start for informed RRT*\n            tree = [start_root]\n            start_root.children = []\n            start_root.cost = 0.0\n\n            # Copy best path into tree\n            prev_node = start_root\n            for pos in best_path[1:]:\n                n_cost = prev_node.cost + self._dist(prev_node.position, pos)\n                new_node = Node(pos, parent=prev_node, cost=n_cost)\n                prev_node.add_child(new_node)\n                tree.append(new_node)\n                nodes.append(new_node)\n                edges.append((prev_node, new_node))\n                prev_node = new_node\n\n            best_goal_node = prev_node\n            best_cost = best_goal_node.cost\n\n            no_improve_count = 0\n            max_no_improve = 120\n            post_opt_iters = self.max_iter // 2\n            c_min = self._dist(start_pos, goal_pos)\n\n            for _ in range(post_opt_iters):\n                if timed_out() or no_improve_count >= max_no_improve:\n                    break\n\n                sample_pt = self._ellipsoidal_informed_sample(best_cost, c_min, start_pos, goal_pos, bounds, obstacles, is_3d)\n                nearest_node = self._nearest(tree, sample_pt)\n                new_pos = self._steer(nearest_node.position, sample_pt)\n\n                if self._is_in_obstacle(new_pos, obstacles, is_3d):\n                    no_improve_count += 1\n                    continue\n                if self._is_edge_in_obstacle(nearest_node.position, new_pos, obstacles, is_3d):\n                    no_improve_count += 1\n                    continue\n\n                near_nodes = self._near(tree, new_pos, self.fixed_radius)\n\n                min_cost = nearest_node.cost + self._dist(nearest_node.position, new_pos)\n                best_parent = nearest_node\n                for near_node in near_nodes:\n                    cost_candidate = near_node.cost + self._dist(near_node.position, new_pos)\n                    if cost_candidate + self.improve_tol < min_cost and not self._is_edge_in_obstacle(near_node.position, new_pos, obstacles, is_3d):\n                        min_cost = cost_candidate\n                        best_parent = near_node\n\n                new_node = Node(new_pos, parent=best_parent, cost=min_cost)\n                best_parent.add_child(new_node)\n                tree.append(new_node)\n                nodes.append(new_node)\n                edges.append((best_parent, new_node))\n\n                rewired = False\n                for near_node in near_nodes:\n                    if near_node == best_parent:\n                        continue\n                    cost_through_new = new_node.cost + self._dist(new_node.position, near_node.position)\n                    if cost_through_new + self.improve_tol < near_node.cost and not self._is_edge_in_obstacle(new_node.position, near_node.position, obstacles, is_3d):\n                        if near_node.parent:\n                            try:\n                                edges.remove((near_node.parent, near_node))\n                            except ValueError:\n                                pass\n                            near_node.parent.remove_child(near_node)\n                        near_node.parent = new_node\n                        near_node.cost = cost_through_new\n                        new_node.add_child(near_node)\n                        edges.append((new_node, near_node))\n                        self._update_costs_recursive(near_node)\n                        rewired = True\n\n                dist_goal = self._dist(new_node.position, goal_pos)\n                if dist_goal <= self.step_size and not self._is_edge_in_obstacle(new_node.position, goal_pos, obstacles, is_3d):\n                    goal_node = Node(goal_pos, parent=new_node, cost=new_node.cost + dist_goal)\n                    new_node.add_child(goal_node)\n                    tree.append(goal_node)\n                    nodes.append(goal_node)\n                    edges.append((new_node, goal_node))\n                    if goal_node.cost + self.improve_tol < best_cost:\n                        best_cost = goal_node.cost\n                        best_goal_node = goal_node\n                        no_improve_count = 0\n                        success_state = True\n                    else:\n                        no_improve_count += 1\n                else:\n                    no_improve_count += 1\n\n                if not rewired:\n                    no_improve_count += 1\n\n            extracted_path = best_goal_node.path_from_root() if success_state else best_path\n            # Post-process path shortcutting for smoothness\n            if len(extracted_path) > 2:\n                extracted_path = self._try_shortcut(extracted_path, obstacles, is_3d)\n        else:\n            extracted_path = best_path\n            success_state = found_solution\n\n        return PlannerResult(success=success_state, path=extracted_path, nodes=nodes, edges=edges)")

class Node:
    def __init__(self, position, parent=None, cost=0.0):
        self.position = position  # Tuple[float, ...]
        self.parent = parent      # Node or None
        self.cost = cost          # Cost from root to this node
        self.children = []

    def add_child(self, child):
        self.children.append(child)
        child.parent = self

    def remove_child(self, child):
        if child in self.children:
            self.children.remove(child)

    def path_from_root(self):
        path = []
        node = self
        while node is not None:
            path.append(node.position)
            node = node.parent
        return path[::-1]
class Planner:
    def __init__(self, max_iter=5000, step_size=5.0):
        self.max_iter = max_iter
        self.step_size = step_size
        self.time_limit = 30.0

        # Fixed radius for neighbor search (tuned empirically)
        self.fixed_radius = 15.0

        # Probability of sampling the goal (goal bias)
        sel

In [ ]:
#1
print("class Node:\n    def __init__(self, position, parent=None):\n        self.position = position\n        self.parent = parent\n        self.children = []\n\n    def add_child(self, child):\n        self.children.append(child)\n        child.parent = self\n\n    def path_from_root(self):\n        path, node = [], self\n        while node:\n            path.append(node.position)\n            node = node.parent\n        return path[::-1]\nclass Planner:\n    def __init__(self, max_iter=5000, step_size=5.0):\n        self.max_iter = max_iter\n        self.step_size = step_size\n\n    def plan(self, map):\n        import random, math\n        bounds = map.size\n        start, goal = map.start, map.goal\n        obstacles = map.obstacles\n        is_3d = len(bounds) == 3\n\n        start_tree = [Node(start)]\n        goal_tree = [Node(goal)]\n        nodes = start_tree + goal_tree\n        edges = []\n\n        def sample_free():\n            while True:\n                p = tuple(random.uniform(0, bounds[d]) for d in range(len(bounds)))\n                if not is_in_obstacle(p):\n                    return p\n\n        def is_in_obstacle(p):\n            for obs in obstacles:\n                if is_3d:\n                    x,y,z,w,h,d = obs\n                    if x <= p[0] <= x+w and y <= p[1] <= y+h and z <= p[2] <= z+d:\n                        return True\n                else:\n                    x,y,w,h = obs\n                    if x <= p[0] <= x+w and y <= p[1] <= y+h:\n                        return True\n            return False\n\n        def is_edge_in_obstacle(p1, p2, resolution=1.0):\n            dist = math.dist(p1, p2)\n            steps = max(1, int(dist / resolution))\n            for i in range(steps+1):\n                interp = tuple(p1[d] + (p2[d]-p1[d]) * i/steps for d in range(len(p1)))\n                if is_in_obstacle(interp):\n                    return True\n            return False\n\n        def nearest(tree, point):\n            return min(tree, key=lambda n: math.dist(n.position, point))\n\n        def steer(from_pos, to_pos):\n            dist = math.dist(from_pos, to_pos)\n            if dist <= self.step_size:\n                return to_pos\n            ratio = self.step_size / dist\n            return tuple(from_pos[d] + ratio * (to_pos[d]-from_pos[d]) for d in range(len(from_pos)))\n\n        def extend(tree, target):\n            nearest_node = nearest(tree, target)\n            new_pos = steer(nearest_node.position, target)\n            if (not is_in_obstacle(new_pos) and not is_edge_in_obstacle(nearest_node.position, new_pos)):\n                new_node = Node(new_pos)\n                nearest_node.add_child(new_node)\n                tree.append(new_node)\n                nodes.append(new_node)\n                edges.append((nearest_node, new_node))\n                return new_node\n            return None\n\n        def connect(tree, target_node):\n            current = nearest(tree, target_node.position)\n            while True:\n                new_pos = steer(current.position, target_node.position)\n                if is_in_obstacle(new_pos) or is_edge_in_obstacle(current.position, new_pos):\n                    return None\n                new_node = Node(new_pos)\n                current.add_child(new_node)\n                tree.append(new_node)\n                nodes.append(new_node)\n                edges.append((current, new_node))\n                if math.dist(new_pos, target_node.position) <= self.step_size:\n                    if not is_edge_in_obstacle(new_pos, target_node.position):\n                        final_node = Node(target_node.position)\n                        new_node.add_child(final_node)\n                        tree.append(final_node)\n                        nodes.append(final_node)\n                        edges.append((new_node, final_node))\n                        return final_node\n                    return None\n                current = new_node\n\n        for i in range(self.max_iter):\n            rand_point = sample_free()\n            tree_a, tree_b = (start_tree, goal_tree) if i % 2 == 0 else (goal_tree, start_tree)\n            new_node = extend(tree_a, rand_point)\n            if new_node is None:\n                continue\n            connected_node = connect(tree_b, new_node)\n            if connected_node:\n                path_a = new_node.path_from_root()\n                path_b = connected_node.path_from_root()\n                full_path = path_a + path_b[::-1]\n                return PlannerResult(True, full_path, nodes, edges)\n\n        return PlannerResult(False, [], nodes, edges)"
)

class Node:
    def __init__(self, position, parent=None):
        self.position = position
        self.parent = parent
        self.children = []

    def add_child(self, child):
        self.children.append(child)
        child.parent = self

    def path_from_root(self):
        path, node = [], self
        while node:
            path.append(node.position)
            node = node.parent
        return path[::-1]
class Planner:
    def __init__(self, max_iter=5000, step_size=5.0):
        self.max_iter = max_iter
        self.step_size = step_size

    def plan(self, map):
        import random, math
        bounds = map.size
        start, goal = map.start, map.goal
        obstacles = map.obstacles
        is_3d = len(bounds) == 3

        start_tree = [Node(start)]
        goal_tree = [Node(goal)]
        nodes = start_tree + goal_tree
        edges = []

        def sample_free():
            while True:
                p = tuple(random.uniform(0, bounds[d]) for d in range(len

In [4]:
#2
print("class Node:\n    def __init__(self, position: Tuple[float, ...], parent=None, cost=0.0):\n        self.position = position\n        self.parent = parent\n        self.cost = cost\n        self.children: List[Node] = []\n        self.valid = True\n        if parent:\n            parent.children.append(self)\n\n    def add_child(self, child):\n        self.children.append(child)\n\n    def remove_child(self, child):\n        try:\n            self.children.remove(child)\n        except ValueError:\n            pass\n\n    def update_parent(self, new_parent, new_cost):\n        if self.parent is not None:\n            self.parent.remove_child(self)\n        self.parent = new_parent\n        self.cost = new_cost\n        new_parent.add_child(self)\n\n    def path_from_root(self) -> List[Tuple[float, ...]]:\n        path = []\n        n = self\n        while n:\n            path.append(n.position)\n            n = n.parent\n        return path[::-1]\nclass Planner:\n    def __init__(self, max_iter: int = 5000, step_size: float = 5.0):\n        self.max_iter = max_iter\n        self.step_size = step_size\n\n    def plan(self, map) -> PlannerResult:\n        start_time = time.monotonic()\n        time_limit = 30.0\n\n        bounds = map.size\n        start_pos = map.start\n        goal_pos = map.goal\n        obstacles = map.obstacles\n        dim = len(bounds)\n        is_3d = (dim == 3)\n\n        def in_bounds(p):\n            return all(0 <= p[d] <= bounds[d] for d in range(dim))\n\n        def dist(a, b):\n            return math.dist(a, b)\n\n        def steer(from_pos, to_pos):\n            vector = tuple(to_pos[d] - from_pos[d] for d in range(dim))\n            length = dist(from_pos, to_pos)\n            if length <= self.step_size:\n                new_p = to_pos\n            else:\n                scale = self.step_size / length\n                new_p = tuple(from_pos[d] + vector[d] * scale for d in range(dim))\n            if in_bounds(new_p):\n                return new_p\n            # Clip if numerics out of bounds\n            clipped = tuple(min(max(new_p[d], 0), bounds[d]) for d in range(dim))\n            return clipped\n\n        def sample_point(iteration):\n            # Dynamic goal bias: decays exponentially from 0.15 to 0.02\n            bias_max = 0.15\n            bias_min = 0.02\n            decay = 0.0005\n            goal_bias = bias_min + (bias_max - bias_min) * math.exp(-decay * iteration)\n            if random.random() < goal_bias:\n                return goal_pos\n            # Uniform sample rejection capped at 100 attempts\n            for _ in range(100):\n                sample = tuple(random.uniform(0, bounds[d]) for d in range(dim))\n                if not self._is_in_obstacle(sample, obstacles, is_3d):\n                    return sample\n            return goal_pos\n\n        def adaptive_radius(iteration, n_nodes):\n            gamma = 40.0\n            if n_nodes < 2:\n                return self.step_size * 6.0\n            rmax = self.step_size * 10\n            rmin = self.step_size * 1.5\n            alpha = min(1.0, iteration / self.max_iter)\n            radius = rmax * (1 - alpha) + rmin * alpha\n            r_theoretical = gamma * ((math.log(n_nodes) / n_nodes) ** (1 / dim))\n            radius = min(radius, max(r_theoretical, rmin))\n            return radius\n\n        # Collision check for a node inside obstacles\n        def collision_node(pos):\n            for obs in obstacles:\n                if is_3d:\n                    x, y, z, w, h, d = obs\n                    px, py, pz = pos\n                    if x <= px <= x + w and y <= py <= y + h and z <= pz <= z + d:\n                        return True\n                else:\n                    x, y, w_, h_ = obs\n                    px, py = pos\n                    if x <= px <= x + w_ and y <= py <= y + h_:\n                        return True\n            return False\n\n        # Collision check for edge between two nodes\n        def collision_edge(a, b, res=1.0):\n            length = dist(a, b)\n            steps = max(1, int(length / res))\n            for i in range(steps + 1):\n                interp = tuple(a[d] + (b[d] - a[d]) * i / steps for d in range(dim))\n                if collision_node(interp):\n                    return True\n            return False\n\n        # Propagate cost updates downstream BFS\n        def propagate_costs(node):\n            queue = [node]\n            while queue:\n                current = queue.pop(0)\n                for c in current.children:\n                    new_cost = current.cost + dist(current.position, c.position)\n                    if new_cost + 1e-12 < c.cost:\n                        c.cost = new_cost\n                        c.parent = current\n                        queue.append(c)\n\n        # Incremental shortcutting progressive improvement\n        def incremental_shortcut(path: List[Tuple[float, ...]]) -> List[Tuple[float, ...]]:\n            if len(path) < 3:\n                return path\n            shortened = [path[0]]\n            i = 0\n            while i < len(path) -1:\n                j = len(path) - 1\n                while j > i+1:\n                    if not collision_edge(path[i], path[j]):\n                        break\n                    j -= 1\n                shortened.append(path[j])\n                i = j\n            return shortened\n\n        # Attempt to connect one tree node to the other tree, optionally extending if needed\n        def connect_trees(node_from: Node, other_tree: List[Node], iteration: int):\n            nonlocal best_cost, best_start_node, best_goal_node, success\n\n            # Find closest node in other_tree\n            nearest_other = min(other_tree, key=lambda n: dist(n.position, node_from.position))\n\n            # If within step size, attempt direct connection\n            if dist(nearest_other.position, node_from.position) <= self.step_size:\n                if not collision_edge(nearest_other.position, node_from.position):\n                    # Connect new node to other tree\n                    new_node = Node(node_from.position)\n                    new_node.update_parent(nearest_other, nearest_other.cost + dist(nearest_other.position, node_from.position))\n                    other_tree.append(new_node)\n                    nodes.append(new_node)\n                    edges.append((nearest_other, new_node))\n\n                    # Update best solution if improved\n                    total = new_node.cost + node_from.cost\n                    if total + 1e-12 < best_cost:\n                        best_cost = total\n                        best_start_node = node_from if node_from in tree_start else new_node\n                        best_goal_node = new_node if new_node in tree_goal else node_from\n                        success = True\n                    return True\n\n            # Otherwise, attempt incremental extensions (max 5 steps)\n            current = nearest_other\n            for _ in range(5):\n                new_pos = steer(current.position, node_from.position)\n                if collision_node(new_pos) or collision_edge(current.position, new_pos):\n                    break\n                if dist(new_pos, current.position) < 1e-6:\n                    break\n                new_node = Node(new_pos)\n                new_node.update_parent(current, current.cost + dist(current.position, new_pos))\n                other_tree.append(new_node)\n                nodes.append(new_node)\n                edges.append((current, new_node))\n                current = new_node\n                # Check if close enough to connect node_from\n                if dist(current.position, node_from.position) <= self.step_size:\n                    if not collision_edge(current.position, node_from.position):\n                        final_node = Node(node_from.position)\n                        final_node.update_parent(current, current.cost + dist(current.position, node_from.position))\n                        other_tree.append(final_node)\n                        nodes.append(final_node)\n                        edges.append((current, final_node))\n                        total = final_node.cost + node_from.cost\n                        if total + 1e-12 < best_cost:\n                            best_cost = total\n                            best_start_node = node_from if node_from in tree_start else final_node\n                            best_goal_node = final_node if final_node in tree_goal else node_from\n                            success = True\n                        return True\n            return False\n\n        # Initialization of trees and data\n        start_root = Node(start_pos)\n        goal_root = Node(goal_pos)\n        tree_start = [start_root]\n        tree_goal = [goal_root]\n        nodes = [start_root, goal_root]\n        edges: List[Tuple[Node, Node]] = []\n\n        best_cost = float('inf')\n        best_start_node = None\n        best_goal_node = None\n        success = False\n\n        for i in range(self.max_iter):\n            if time.monotonic() - start_time > time_limit:\n                break\n\n            # Alternate expanding trees\n            if i % 2 == 0:\n                tree_a, tree_b = tree_start, tree_goal\n            else:\n                tree_a, tree_b = tree_goal, tree_start\n\n            # Sample with decaying goal bias\n            q_rand = sample_point(i)\n\n            # Nearest node in tree_a to q_rand\n            nearest = min(tree_a, key=lambda n: dist(n.position, q_rand))\n            q_new_pos = steer(nearest.position, q_rand)\n            if collision_node(q_new_pos) or collision_edge(nearest.position, q_new_pos) or not in_bounds(q_new_pos):\n                continue\n\n            r = adaptive_radius(i, len(nodes))\n            neighbors = [n for n in tree_a if dist(n.position, q_new_pos) <= r]\n\n            # Select best parent minimizing cost + edge length, with collision checked\n            min_cost = nearest.cost + dist(nearest.position, q_new_pos)\n            best_parent = nearest\n            for nbr in neighbors:\n                cost_via = nbr.cost + dist(nbr.position, q_new_pos)\n                if cost_via + 1e-12 < min_cost and not collision_edge(nbr.position, q_new_pos):\n                    best_parent = nbr\n                    min_cost = cost_via\n\n            new_node = Node(q_new_pos)\n            new_node.update_parent(best_parent, min_cost)\n            tree_a.append(new_node)\n            nodes.append(new_node)\n            edges.append((best_parent, new_node))\n\n            # Rewiring neighbors if cheaper via new_node\n            for nbr in neighbors:\n                if nbr is best_parent:\n                    continue\n                cost_through_new = new_node.cost + dist(new_node.position, nbr.position)\n                if cost_through_new + 1e-12 < nbr.cost and not collision_edge(new_node.position, nbr.position):\n                    try:\n                        edges.remove((nbr.parent, nbr))\n                    except ValueError:\n                        pass\n                    nbr.update_parent(new_node, cost_through_new)\n                    edges.append((new_node, nbr))\n                    propagate_costs(nbr)\n\n            # Attempt to connect newly added node to the other tree\n            connected = connect_trees(new_node, tree_b, i)\n\n            # On successful connection, incrementally shortcut improved paths\n            if success:\n                path_start = best_start_node.path_from_root()\n                path_goal = best_goal_node.path_from_root()\n                combined_path = path_start + path_goal[-2::-1] if path_goal else path_start\n                combined_path = incremental_shortcut(combined_path)\n                return PlannerResult(True, combined_path, nodes, edges)\n\n        # If no path found but nodes exist in start tree, return best partial path toward goal\n        if success:\n            path_start = best_start_node.path_from_root()\n            path_goal = best_goal_node.path_from_root()\n            combined_path = path_start + path_goal[-2::-1] if path_goal else path_start\n            combined_path = incremental_shortcut(combined_path)\n            return PlannerResult(True, combined_path, nodes, edges)\n\n        # If no success, attempt fallback path to node closest to goal in start tree if any\n        closest = None\n        min_dist = float('inf')\n        for node in tree_start:\n            d_ = dist(node.position, goal_pos)\n            if d_ < min_dist:\n                min_dist = d_\n                closest = node\n        fallback_path = []\n        if closest is not None:\n            cur = closest\n            while cur:\n                fallback_path.append(cur.position)\n                cur = cur.parent\n            fallback_path.reverse()\n        else:\n            fallback_path = [start_pos]\n\n        return PlannerResult(False, fallback_path, nodes, edges)\n\n    def _is_in_obstacle(self, pos, obstacles, is_3d):\n        for obs in obstacles:\n            if is_3d:\n                x, y, z, w, h, d = obs\n                px, py, pz = pos\n                if x <= px <= x + w and y <= py <= y + h and z <= pz <= z + d:\n                    return True\n            else:\n                x, y, w_, h_ = obs\n                px, py = pos\n                if x <= px <= x + w_ and y <= py <= y + h_:\n                    return True\n        return False\n\n    def _is_edge_in_obstacle(self, from_pos, to_pos, obstacles, is_3d, resolution=1.0):\n        distance = math.dist(from_pos, to_pos)\n        steps = max(1, int(distance / resolution))\n        for i in range(steps + 1):\n            interp = tuple(from_pos[d] + (to_pos[d] - from_pos[d]) * (i / steps) for d in range(len(from_pos)))\n            if self._is_in_obstacle(interp, obstacles, is_3d):\n                return True\n        return False"
)

class Node:
    def __init__(self, position: Tuple[float, ...], parent=None, cost=0.0):
        self.position = position
        self.parent = parent
        self.cost = cost
        self.children: List[Node] = []
        self.valid = True
        if parent:
            parent.children.append(self)

    def add_child(self, child):
        self.children.append(child)

    def remove_child(self, child):
        try:
            self.children.remove(child)
        except ValueError:
            pass

    def update_parent(self, new_parent, new_cost):
        if self.parent is not None:
            self.parent.remove_child(self)
        self.parent = new_parent
        self.cost = new_cost
        new_parent.add_child(self)

    def path_from_root(self) -> List[Tuple[float, ...]]:
        path = []
        n = self
        while n:
            path.append(n.position)
            n = n.parent
        return path[::-1]
class Planner:
    def __init__(self, max_iter: int = 5000, step_size: fl

In [142]:
# merged_df[merged_df['success_rate']>=1.0].sort_values(by='length_improvement', ascending=False)

In [155]:
# raw_merged_df[raw_merged_df['map_id']==1].sort_values(by='objective_score', ascending=False)

### Compare DB

In [ ]:
time_db_path_dict = dict()
time_db_path_dict['ma_t_1'] = "./paper_result/interactive_multi_agent1/db/time_db.json"
time_db_path_dict['ma_t_2'] = "./paper_result/interactive_multi_agent2/db/time_db.json"
time_db_path_dict['ma_t_3'] = "./paper_result/interactive_multi_agent3/db/time_db.json"
time_db_path_dict['ma_t_4'] = "./paper_result/interactive_multi_agent4/db/time_db.json"
time_db_path_dict['ma_t_5'] = "./paper_result/interactive_multi_agent5/db/time_db.json"
time_db_path_dict['ma_t_6'] = "./paper_result/interactive_multi_agent_ref_perform/db/time_db.json"
time_db_path_dict['gpt5'] = "./paper_result/interactive_multi_agent_gpt5/db/path_db.json"


In [96]:
time_result_dfs = {}

for k, path in time_db_path_dict.items():
    res = get_exp_result(path, ref_avg, time_limit=30.0)
    time_result_dfs[k] = res

[2025.09.18 - 17:28:34] Map 1
Iteration 1: Time taken: 0.0160 seconds, Success: True
Iteration 2: Time taken: 0.0156 seconds, Success: True
Iteration 3: Time taken: 0.0070 seconds, Success: True
Iteration 4: Time taken: 0.0128 seconds, Success: True
Iteration 5: Time taken: 0.0165 seconds, Success: True
Iteration 6: Time taken: 0.0085 seconds, Success: True
Iteration 7: Time taken: 0.0150 seconds, Success: True
Iteration 8: Time taken: 0.0074 seconds, Success: True
Iteration 9: Time taken: 0.0135 seconds, Success: True
Iteration 10: Time taken: 0.0135 seconds, Success: True
Iteration 11: Time taken: 0.0110 seconds, Success: True
Iteration 12: Time taken: 0.0287 seconds, Success: True
Iteration 13: Time taken: 0.0131 seconds, Success: True
Iteration 14: Time taken: 0.0189 seconds, Success: True
Iteration 15: Time taken: 0.0185 seconds, Success: True
Iteration 16: Time taken: 0.0207 seconds, Success: True
Iteration 17: Time taken: 0.0100 seconds, Success: True
Iteration 18: Time taken: 0

In [104]:
frames = list()
raw_frames = list()

for k, df in time_result_dfs.items():
    print(df.empty)
    if df.empty:
        continue
    grouped_df = df.groupby('alg_name').mean(numeric_only=True).reset_index()
    grouped_df['method'] = k
    frames.append(grouped_df)
    df['method'] = k
    raw_frames.append(df)

time_merged_df = pd.concat([a]+frames, ignore_index=True, axis=0)
time_raw_merged_df = pd.concat(raw_frames, ignore_index=True, axis=0)

False
False
False
False
True
True


In [106]:
time_merged_df.sort_values(by='time_improvement', ascending=False)

map_id  success_rate  time_avg  num_nodes_avg  path_length_avg  \
0      1.0      1.000000  0.006919     155.170000       213.941368   
12     1.0      1.000000  0.011491     183.400000       217.737710   
9      1.0      1.000000  0.014536     197.896667       219.650364   
14     1.0      1.000000  0.017669     192.850000       179.451081   
11     1.0      1.000000  0.020147     233.856667       197.031716   
8      1.0      1.000000  0.020182     227.040000       187.996802   
13     1.0      1.000000  0.019356     242.916667       199.463439   
10     1.0      1.000000  0.022593     244.360000       177.578789   
15     1.0      1.000000  0.023254     316.660000       174.402637   
18     1.0      1.000000  0.026760     338.270000       185.285031   
1      1.0      1.000000  0.028223     175.796667       186.840439   
19     1.0      1.000000  0.029423     218.220000       179.654992   
20     1.0      1.000000  0.030848     224.786667       178.826838   
17     1.0      1.000000  0.031542     262.053333       178.022057   
22     1.0      1.000000  0.036686     110.996667       184.162923   
21     1.0      1.000000  0.037199     102.100000       177.960308   
24     1.0      1.000000  0.042410     201.373333       179.204613   
16     1.0      0.996667  0.035789     328.723333       171.274813   
23     1.0      1.000000  0.049790     213.186667       177.789994   
6      1.0      1.000000  0.105181     986.326667       214.254234   
7      1.0      1.000000  0.208390     958.216667       166.655759   
3      1.0      1.000000  0.144748     518.830000       170.811093   
2      1.0      1.000000  0.148262     500.273333       171.859631   
4      1.0      1.000000  0.282802     930.400000       161.982690   
5      1.0      1.000000  0.656565     541.140000       165.450936   

    smoothness_avg  success_improvement  time_improvement  node_improvement  \
0         0.010032             0.000000         91.632975         83.730304   
12        0.011060             0.000000         83.628578         79.380468   
9         0.010883             0.000000         80.080783         77.792148   
14        0.025495             0.000000         75.608330         78.636481   
11        0.014623             0.000000         72.399989         73.722360   
8         0.016492             0.000000         72.127880         74.107393   
13        0.014069             0.000000         71.844634         71.869590   
10        0.081882             0.000000         70.122536         73.148253   
15        0.104016             0.000000         64.953376         63.275932   
18        0.019129             0.000000         62.068205         60.666767   
1         0.016921             0.000000         61.852747         81.194264   
19        0.023746             0.000000         60.767497         75.611388   
20        0.023936             0.000000         59.091639         75.067627   
17        0.023196             0.000000         56.772417         70.574772   
22        0.018625             0.000000         48.329378         85.378822   
21        0.023726             0.000000         47.901014         86.766129   
24        0.070746             0.000000         45.635880         78.422157   
16        0.086853            -0.333333         42.355638         59.746490   
23        0.105755             0.000000         27.612048         75.749613   
6         0.005997             0.000000          0.000000          0.000000   
7         0.015543             0.000000        -98.060014          3.598092   
3         0.030153             0.000000       -128.880400         40.361656   
2         0.029741             0.000000       -172.365749         36.459870   
4         0.030676             0.000000       -330.503418        -10.049902   
5         0.044705             0.000000      -1118.219344         32.171246   

    length_improvement  smoothness_improvement  objective_score  alg_name  \
0            -0.007719               67.326861     

In [ ]:
path_db_path_dict = dict()
# path_db_path_dict['ma_p_1'] = "./paper_result/interactive_multi_agent1/db/path_db.json"
# path_db_path_dict['ma_p_2'] = "./paper_result/interactive_multi_agent2/db/path_db.json"
# path_db_path_dict['ma_p_3'] = "./paper_result/interactive_multi_agent3/db/path_db.json"
# path_db_path_dict['ma_p_4'] = "./paper_result/interactive_multi_agent4/db/path_db.json"
# path_db_path_dict['ma_p_5'] = "./paper_result/interactive_multi_agent5/db/path_db.json"
# path_db_path_dict['ma_p_6'] = "./paper_result/interactive_multi_agent_ref_perform/db/path_db.json"
path_db_path_dict['gpt5'] = "./paper_result/interactive_multi_agent_gpt5/db/path_db.json"


In [40]:
path_result_dfs = {}

for k, path in time_db_path_dict.items():
    # res = get_exp_result(path, ref_avg, time_limit=50.0)
    res = get_exp_result(path, ref_avg, length_limit=20.0)
    path_result_dfs[k] = res

NameError: name 'time_db_path_dict' is not defined

In [ ]:
frames = list()
raw_frames = list()

for k, df in time_result_dfs.items():
    print(df.empty)
    if df.empty:
        continue
    grouped_df = df.groupby('alg_name').mean(numeric_only=True).reset_index()
    grouped_df['method'] = k
    frames.append(grouped_df)
    df['method'] = k
    raw_frames.append(df)

path_merged_df = pd.concat([a]+frames, ignore_index=True, axis=0)
path_raw_merged_df = pd.concat(raw_frames, ignore_index=True, axis=0)

In [ ]:
path_merged_df.sort_values(by='time_improvement', ascending=False)

### Compare all

In [56]:
entire_db_path_dict = dict()

entire_db_path_dict['gp5'] = "./paper_result/interactive_multi_agent_gpt5/results/pops/evaluated_entire_population_generation.json"

In [ ]:
entire_result_dfs = {}

for k, path in entire_db_path_dict.items():
    res = get_exp_result(path, ref_avg, time_limit=70.0, length_limit=24.0, is_or=True)
    entire_result_dfs[k] = res

655
Evaluating method 1/655: -47.53913
[2025.09.26 - 12:35:23] Map 1
Iteration 1: Time taken: 0.0135 seconds, Success: True
Iteration 2: Time taken: 0.0060 seconds, Success: True
Iteration 3: Time taken: 0.0060 seconds, Success: True
Iteration 4: Time taken: 0.0040 seconds, Success: True
Iteration 5: Time taken: 0.0000 seconds, Success: True
Iteration 6: Time taken: 0.0172 seconds, Success: True
Iteration 7: Time taken: 0.0060 seconds, Success: True
Iteration 8: Time taken: 0.0067 seconds, Success: True
Iteration 9: Time taken: 0.0030 seconds, Success: True
Iteration 10: Time taken: 0.0114 seconds, Success: True
Iteration 11: Time taken: 0.0009 seconds, Success: True
Iteration 12: Time taken: 0.0000 seconds, Success: True
Iteration 13: Time taken: 0.0199 seconds, Success: True
Iteration 14: Time taken: 0.0060 seconds, Success: True
Iteration 15: Time taken: 0.0048 seconds, Success: True
Iteration 16: Time taken: 0.0000 seconds, Success: True
Iteration 17: Time taken: 0.0149 seconds, Su

KeyboardInterrupt: 

In [41]:
l_entire_result_dfs = {}

for k, path in entire_db_path_dict.items():
    # res = get_exp_result(path, ref_avg, time_limit=50.0)
    res = get_exp_result(path, ref_avg, length_limit=20.0)
    l_entire_result_dfs[k] = res

[2025.09.22 - 13:35:29] Map 1
Iteration 1: Time taken: 0.0143 seconds, Success: True
Iteration 2: Time taken: 0.0130 seconds, Success: True
Iteration 3: Time taken: 0.0060 seconds, Success: True
Iteration 4: Time taken: 0.0208 seconds, Success: True
Iteration 5: Time taken: 0.0067 seconds, Success: True
Iteration 6: Time taken: 0.0204 seconds, Success: True
Iteration 7: Time taken: 0.0141 seconds, Success: True
Iteration 8: Time taken: 0.0145 seconds, Success: True
Iteration 9: Time taken: 0.0000 seconds, Success: True
Iteration 10: Time taken: 0.0259 seconds, Success: True
Iteration 11: Time taken: 0.0060 seconds, Success: True
Iteration 12: Time taken: 0.0205 seconds, Success: True
Iteration 13: Time taken: 0.0119 seconds, Success: True
Iteration 14: Time taken: 0.0162 seconds, Success: True
Iteration 15: Time taken: 0.0045 seconds, Success: True
Iteration 16: Time taken: 0.0115 seconds, Success: True
Iteration 17: Time taken: 0.0167 seconds, Success: True
Iteration 18: Time taken: 0

In [63]:
entire_result_dfs

{}

In [62]:
frames = list()
raw_frames = list()

for k, df in entire_result_dfs.items():
    print(df.empty)
    if df.empty:
        continue
    grouped_df = df.groupby('alg_name').mean(numeric_only=True).reset_index()
    grouped_df['method'] = k
    frames.append(grouped_df)
    df['method'] = k
    raw_frames.append(df)

entire_merged_df = pd.concat([a]+frames, ignore_index=True, axis=0)
entire_raw_merged_df = pd.concat(raw_frames, ignore_index=True, axis=0)

ValueError: No objects to concatenate

In [ ]:
entire_merged_df

In [39]:
entire_merged_df.sort_values(by='time_improvement', ascending=False)

alg_name  map_id  success_rate  time_avg  \
0                        BI-RRT   1.000         1.000     0.007   
23                      -35.390   1.000         1.000     0.010   
18                      -37.181   1.000         1.000     0.019   
9                   RRT-Connect   1.000         1.000     0.014   
10                      -40.793   1.000         1.000     0.017   
39                      -31.932   1.000         1.000     0.017   
15                      -38.511   1.000         1.000     0.015   
12                      -39.958   1.000         1.000     0.018   
25                      -34.706   1.000         0.993     0.016   
14                      -39.022   1.000         1.000     0.024   
33                      -32.875   1.000         1.000     0.024   
32                      -32.968   1.000         1.000     0.018   
17                      -37.598   1.000         1.000     0.020   
16                      -37.606   1.000         1.000     0.027   
8                  RRT*-Connect   1.000         1.000     0.020   
11                      -40.134   1.000         1.000     0.028   
29                      -33.377   1.000         1.000     0.018   
19                      -37.091   1.000         1.000     0.027   
20                      -36.947   1.000         1.000     0.025   
37                      -32.126   1.000         0.993     0.021   
21                      -36.918   1.000         1.000     0.022   
28                      -33.560   1.000         1.000     0.021   
47                      -26.291   1.000         1.000     0.017   
13                      -39.287   1.000         1.000     0.023   
22                      -35.788   1.000         0.987     0.020   
45                      -30.119   1.000         1.000     0.022   
30                      -33.079   1.000         1.000     0.023   
43                      -30.407   1.000         1.000     0.028   
35                      -32.673   1.000         0.973     0.025   
41                      -31.057   1.000         1.000     0.022   
24                      -35.013   1.000         1.000     0.027   
31                      -33.039   1.000         1.000     0.021   
27                      -33.746   1.000         1.000     0.030   
40                      -31.192   1.000         0.987     0.023   
48                      -14.397   1.000         0.993     0.029   
44                      -30.289   1.000         1.000     0.034   
36                      -32.241   1.000         1.000     0.030   
1                       BI-RRT*   1.000         1.000     0.028   
49                      -13.571   1.000         1.000     0.033   
34                      -32.814   1.000         1.000     0.026   
50                       32.437   1.000         0.860     0.022   
38                      -32.047   1.000         0.997     0.027   
26                      -34.172   1.000         0.997     0.034   
42                      -30.874   1.000         1.000     0.030   
46                      -29.115   1.000         0.990     0.025   
6                           RRT   1.000         1.000     0.102   
7                          RRT*   1.000         1.000     0.203   
3         Improved-RRT*-Connect   1.000         1.000     0.142   
2   Bidirectional-Informed-RRT*   1.000         1.000     0.145   
4                 Informed-RRT*   1.000         1.000     0.276   
5         Informed-RRT*-Connect   1.000         1.000     0.624   

    num_nodes_avg  path_length_avg  smoothness_avg  success_improvement  \
0         155.170          213.941           0.010                0.000   
23        148.697          194.558           0.097                0.000   
18         95.667          179.157           0.083                0.000   
9         197.897          219.650           0.011                0.000   
10        152.000          181.445           0.141                0.000   
39         72.000          194.303           0.104                0.000   
15        105

In [44]:
entire_merged_df.sort_values(by='length_improvement', ascending=False)

alg_name  map_id  success_rate  time_avg  \
64                      795.613   1.000         1.000     1.141   
65                      903.659   1.000         1.000     1.081   
63                      705.123   1.000         1.000     1.068   
50                      192.475   1.000         0.997     0.391   
61                      435.395   1.000         1.000     0.818   
35                       83.187   1.000         1.000     0.272   
56                      309.439   1.000         1.000     0.686   
47                      166.231   1.000         1.000     0.309   
48                      175.428   1.000         0.960     0.509   
44                      139.640   1.000         1.000     0.329   
4                 Informed-RRT*   1.000         1.000     0.276   
39                       98.451   1.000         1.000     0.262   
51                      198.604   1.000         1.000     0.338   
46                      164.246   1.000         1.000     0.451   
49                      178.588   1.000         0.933     0.376   
37                       93.887   1.000         1.000     0.232   
55                      296.978   1.000         1.000     0.604   
59                      390.035   1.000         0.993     0.485   
16                      -11.328   1.000         1.000     0.070   
36                       84.086   1.000         1.000     0.236   
52                      214.294   1.000         0.997     0.304   
33                       47.740   1.000         0.993     0.151   
31                       44.323   1.000         1.000     0.236   
25                       21.687   1.000         1.000     0.116   
57                      330.317   1.000         1.000     0.654   
22                       13.790   1.000         1.000     0.112   
15                      -29.845   1.000         1.000     0.067   
5         Informed-RRT*-Connect   1.000         1.000     0.624   
42                      112.111   1.000         0.970     0.334   
41                      107.561   1.000         1.000     0.286   
34                       55.459   1.000         0.967     0.120   
53                      229.277   1.000         1.000     0.352   
54                      276.304   1.000         1.000     0.549   
32                       46.866   1.000         0.997     0.164   
58                      377.492   1.000         1.000     0.510   
11                      -39.958   1.000         1.000     0.018   
43                      112.714   1.000         1.000     0.245   
30                       38.902   1.000         1.000     0.156   
26                       23.108   1.000         1.000     0.106   
28                       27.269   1.000         1.000     0.138   
23                       16.875   1.000         0.997     0.101   
18                       -4.407   1.000         1.000     0.089   
38                       97.373   1.000         1.000     0.268   
40                       99.874   1.000         1.000     0.247   
10                      -40.134   1.000         1.000     0.027   
60                      404.597   1.000         1.000     0.630   
24                       17.170   1.000         1.000     0.139   
27                       24.464   1.000         1.000     0.146   
7                          RRT*   1.000         1.000     0.203   
12                      -39.022   1.000         1.000     0.024   
19                       -3.712   1.000         0.993     0.075   
13                      -37.091   1.000         1.000     0.027   
62                      542.464   1.000         0.997     0.732   
14                      -35.013   1.000         1.000     0.027   
21                       13.671   1.000         1.000     0.175   
45                      144.975   1.000         1.000     0.241   
20                       10.020   1.000         0.997     0.086   
17                      -11.318   1.000         1.000     0.076   
29                       31.176   1.000         1.000     0.159   
3  

### Evolution Trend

In [175]:
def reset_obj_score(method):
    maps = [multi_obs_map, maze_map, narrow_map]
    benchmarker = MultiMapBenchmarker(maps=maps, iter=10)

    g_total_df = pd.DataFrame()

    code_string = method['code']
    namedf = pd.DataFrame()
    namedf['alg_name'] = [method['objective']]* len(maps)
    with warnings.catch_warnings():
        warnings.simplefilter("ignore")
        planning_module = types.ModuleType("planning_module")
        exec(import_string+code_string, planning_module.__dict__)
        sys.modules[planning_module.__name__] = planning_module
        try:
            planner = planning_module.Planner(max_iter=5000)
        except:
            pass
        res, avg_rest = benchmarker.run(planner.plan)
        
        if avg_rest is None: return 9999
        imp_res = MultiMapBenchmarker.get_improvement(ref_avg, avg_rest)

        # res_df = pd.concat([namedf, avg_rest, imp_res], axis=1)
        # g_total_df = pd.concat([g_total_df, res_df], axis=0)

        return -imp_res['objective_score'].mean()

def get_best_pop(path):
    alg_save = []

    for i in range(1,11):
        pop_path = f"{path}/population_generation_{i}.json"
        tmp_alg = []
        if os.path.exists(pop_path):
            with open(pop_path, "r") as f:
                data = json.load(f)
                tmp_alg = sorted(
                [alg for alg in data if alg.get('operator') != 'initial'],
                key=lambda x: x.get('objective', float('inf'))
                )
            new_tmp_alg = []
            for i, alg in enumerate(tmp_alg[:10]):
                tmp_alg[i]['objective'] = reset_obj_score(alg)
                new_tmp_alg.append(tmp_alg[i])
                
            new_tmp_alg = sorted(
                [alg for alg in data if alg.get('operator') != 'initial'],
                key=lambda x: x.get('objective', float('inf')))
            
            alg_save.append(new_tmp_alg[0])

    return alg_save

def enforce_non_decreasing(arr):
    if not arr:
        return []

    result = [arr[0]]  # 첫 번째 값은 그대로
    for i in range(1, len(arr)):
        if arr[i]['objective'] > result[-1]['objective']:
            result.append(result[-1])   # 이전 값 유지
        else:
            result.append(arr[i])       # 현재 값 유지
    return result

In [193]:
def get_trend_plot(l_dict):
    
    name = list(l_dict.keys())
    alg_list = list(l_dict.values())
    
    fig = go.Figure()

    # name = ['EoH', 'Expert DB(Ours)', 'Expert+Analysis DB(Ours)', 'RAG']
    # p_list = []
    # p_list.append(["top center"]+["bottom center"]+["top center"]*8)
    # p_list.append(["bottom center"]+["top center"]*9)
    # p_list.append(["bottom center"]+["top center"]*7+["bottom center"]*2)
    # p_list.append(["bottom center"]+["top center"]*7+["bottom center"]*2)

    for i, alg in enumerate(alg_list):
        fig.add_trace(go.Scatter(
            x=[i+1 for i in range(len(alg))],
            y=[-x['objective'] for x in alg],
            mode="lines+markers+text",
            text=["{:.2f}".format(-x['objective']) for x in alg],           # 표시할 텍스트 값
            # textposition=p_list[i],
            name=name[i],
            hovertemplate="Step: %{x}<br>Objective: %{y}<br>Operator: {}"
        ))

    fig.update_layout(
        width=800,    # 가로 크기 (px)
        height=500,   # 세로 크기 (px)
    )


    # 레이아웃
    fig.update_layout(
        # title="Objective over Number of Generations",
        xaxis_title="Number of generations",
        yaxis_title="Objective",
        template="plotly_white",
        legend_title="Method"
    )
    fig.update_layout(
        legend=dict(
            x=0.85,   # 가로 위치 (0=왼쪽, 1=오른쪽)
            y=0.1,  # 세로 위치 (0=아래, 1=위)
            bgcolor="rgba(255,255,255,0.7)",  # 배경 색상 (투명도 조절)
            bordercolor="black",              # 테두리 색상
            borderwidth=1
        )
    )
    fig.update_layout(
        xaxis=dict(
            showline=True,          # 축 라인 표시
            linewidth=2,            # 축 라인 두께
            linecolor="black",      # 축 라인 색
            showgrid=True,          # 그리드 표시 여부
            gridcolor="lightgray",  # 그리드 색상
            tickmode="linear",      # 눈금 방식 (linear / array / auto)
            dtick=1,                # 눈금 간격 (예: 1씩 증가)
            tickangle=0,            # 눈금 글자 각도
            tickfont=dict(size=12)  # 눈금 글자 크기
        )
    )
    fig.update_layout(
        yaxis=dict(
            showline=True,          # 축 라인 표시
            linewidth=2,            # 축 라인 두께
            linecolor="black",      # 축 라인 색
            showgrid=True,          # 그리드 표시 여부
            gridcolor="lightgray",  # 그리드 색상
            tickmode="linear",      # 눈금 방식 (linear / array / auto)
            dtick=5,                # 눈금 간격 (예: 1씩 증가)
            tickangle=0,            # 눈금 글자 각도
            tickfont=dict(size=12)  # 눈금 글자 크기
        )
    )
    fig.show()

In [ ]:
trend_db_path_dict = dict()

trend_db_path_dict['EoH'] = "./path_planning/basic_eoh/results/pops"
trend_db_path_dict['Expert'] = "./path_planning/mobj1/results/pops"
trend_db_path_dict['analysis'] = "./path_planning/mobj_analysis/results/pops"
trend_db_path_dict['rag'] = "./path_planning/rag/results/pops"
trend_db_path_dict['ma_e'] = "./paper_result/interactive_multi_agent2/results/pops"
# trend_db_path_dict['ma_e_6'] = "./paper_result/interactive_multi_agent_ref_perform/results/pops"
trend_db_path_dict['gpt5'] = "./paper_result/interactive_multi_agent_gpt5/results/pops"

In [181]:
trend_l_dict = {}

for k,path in trend_db_path_dict.items():
    if trend_l_dict[k]: continue
    print(f"{k} Processing")
    trend_l_dict[k] = enforce_non_decreasing(get_best_pop(path))

ma_e_1 Processing
[2025.09.18 - 21:56:31] Map 1
Iteration 1: Time taken: 0.0283 seconds, Success: True
Iteration 2: Time taken: 0.0111 seconds, Success: True
Iteration 3: Time taken: 0.0150 seconds, Success: True
Iteration 4: Time taken: 0.0141 seconds, Success: True
Iteration 5: Time taken: 0.0151 seconds, Success: True
Iteration 6: Time taken: 0.0080 seconds, Success: True
Iteration 7: Time taken: 0.0193 seconds, Success: True
Iteration 8: Time taken: 0.0261 seconds, Success: True
Iteration 9: Time taken: 0.0175 seconds, Success: True
Iteration 10: Time taken: 0.0196 seconds, Success: True
[2025.09.18 - 21:56:31] Map 2
Iteration 1: Time taken: 0.0418 seconds, Success: True
Iteration 2: Time taken: 0.0351 seconds, Success: True
Iteration 3: Time taken: 0.0255 seconds, Success: True
Iteration 4: Time taken: 0.0241 seconds, Success: True
Iteration 5: Time taken: 0.0495 seconds, Success: True
Iteration 6: Time taken: 0.0206 seconds, Success: True
Iteration 7: Time taken: 0.0402 seconds, 

In [179]:
trend_l_dict

{'EoH': [{'operator': 'm2',
   'algorithm_description': 'This algorithm improves bidirectional RRT by tuning key parameters: reducing step size for finer node expansions, increasing maximum iterations for thorough search, and biasing sampling towards the goal to enhance convergence speed. It also integrates a goal bias sampling with a certain probability to direct growth towards the goal, and employs shortened collision checking resolution to enhance accuracy. Additionally, path smoothing is applied post planning to improve path quality and smoothness.',
   'planning_mechanism': 'The planner grows two trees from start and goal simultaneously, alternately expanding each tree towards sampled points. Sampling is biased towards the goal to increase success and convergence speed. Collision checks are strictly enforced for nodes and edges before insertion. When trees connect, the path is reconstructed and then smoothed by shortcutting to reduce unnecessary detours, resulting in improved path

In [194]:
get_trend_plot(trend_l_dict)